In [1]:
import os
import csv
import pandas as pd
import altair as alt
import geopandas as gpd

import crawl_realestate_data

In [2]:
# Fetch dataset
map_data_filename = "mapdata_002_005.csv"
fetch_dataset = False

if fetch_dataset:
    crawl_realestate_data.main(
        dst_name=map_data_filename,
        resolution_lat=0.002,
        resolution_lon=0.005,
        sleep_time_secs=0.05,
        verbose=True
    )

In [3]:
# Load dataset
with open(map_data_filename) as map_data_f:
    map_data = [row for row in csv.DictReader(map_data_f)]

map_df = pd.DataFrame(data=map_data)
map_df.head(5)

TopLeftLat          TopLeftLon BottomRightLat      BottomRightLon  \
0  59.415335           17.868951      59.413335  17.873950999999998   
1  59.415335  17.873950999999998      59.413335  17.878950999999997   
2  59.415335  17.878950999999997      59.413335  17.883950999999996   
3  59.415335  17.883950999999996      59.413335  17.888950999999995   
4  59.415335  17.888950999999995      59.413335  17.893950999999994   

  WeightPrice WeightSqr    Price PriceSqr Hits PointsForSqrPriceInterval  \
0           4         3  2370000    43000   14                        25   
1           0         0        0        0    0                         0   
2           0         0        0        0    0                         0   
3           0         0        0        0    0                         0   
4           0         0        0        0    0                         0   

  PointsForPriceInterval PointsForZoom PointsForDays PointsForHits  \
0                     30             0            -5            20   
1                      0             0             0             0   
2                      0             0             0             0   
3                      0             0             0             0   
4                      0             0             0             0   

  PointsForDistance SumPointsPrice SumPointsSqr  
0                20             65           60  
1                 0              0            0  
2                 0              0            0  
3                 0              0            0  
4                 0              0            0

In [4]:
# Basic dataset transformations
map_df = map_df.apply(pd.to_numeric)
map_df["CenterLat"] = (map_df["TopLeftLat"] + map_df["BottomRightLat"]) / 2
map_df["CenterLon"] = (map_df["TopLeftLon"] + map_df["BottomRightLon"]) / 2
map_df["PriceVariance"] = map_df["WeightSqr"].max() - map_df["WeightSqr"] + 1
map_df["GoogleMaps"] = map_df.apply(lambda row: f"https://www.google.com/maps/place/{row['CenterLat']},{row['CenterLon']}", axis=1)
map_df.head(5)

TopLeftLat  TopLeftLon  BottomRightLat  BottomRightLon  WeightPrice  \
0   59.415335   17.868951       59.413335       17.873951            4   
1   59.415335   17.873951       59.413335       17.878951            0   
2   59.415335   17.878951       59.413335       17.883951            0   
3   59.415335   17.883951       59.413335       17.888951            0   
4   59.415335   17.888951       59.413335       17.893951            0   

   WeightSqr    Price  PriceSqr  Hits  PointsForSqrPriceInterval  ...  \
0          3  2370000     43000    14                         25  ...   
1          0        0         0     0                          0  ...   
2          0        0         0     0                          0  ...   
3          0        0         0     0                          0  ...   
4          0        0         0     0                          0  ...   

   PointsForZoom  PointsForDays  PointsForHits  PointsForDistance  \
0              0             -5             20                 20   
1              0              0              0                  0   
2              0              0              0                  0   
3              0              0              0                  0   
4              0              0              0                  0   

   SumPointsPrice  SumPointsSqr  CenterLat  CenterLon  PriceVariance  \
0              65            60  59.414335  17.871451              2   
1               0             0  59.414335  17.876451              5   
2               0             0  59.414335  17.881451              5   
3               0             0  59.414335  17.886451              5   
4               0             0  59.414335  17.891451              5   

                                          GoogleMaps  
0  https://www.google.com/maps/place/59.414334999...  
1  https://www.google.com/maps/place/59.414334999...  
2  https://www.google.com/maps/place/59.414334999...  
3  https://www.google.com/maps/place/59.414334999...  
4  https://www.google.com/maps/place/59.414334999...  

[5 rows x 21 columns]

In [5]:
# Let's have a look at price/sqm distribution

# Altair plots limit to 5k rows by default
sample_df = map_df.sample(5000) if map_df.shape[0] > 5000 else map_df
alt.Chart(sample_df).mark_bar().encode(
    alt.X("PriceSqr:Q", bin=alt.Bin(step=10000)),
    y='count()',
)

alt.Chart(...)

In [6]:
# Remove rows with unknown prices
map_df = map_df[map_df.PriceSqr != 0]

# Clip the prices to 1-95 percentile
upper_percentile = map_df["PriceSqr"].quantile(0.95)
lower_percentile = map_df["PriceSqr"].quantile(0.01)
print("Quantiles 1%: ", lower_percentile, ", 95%: ", upper_percentile)

map_df.loc[map_df["PriceSqr"] > upper_percentile, "PriceSqr"] = upper_percentile
map_df.loc[map_df["PriceSqr"] < lower_percentile, "PriceSqr"] = lower_percentile

# Let's have a look at price/sqm distribution again
alt.Chart(map_df).mark_bar().encode(
    alt.X("PriceSqr:Q", bin=alt.Bin(extent=[lower_percentile, upper_percentile], step=2000)),
    y='count()',
)

Quantiles 1%:  28000.0 , 95%:  91000.0


alt.Chart(...)

In [7]:
# Plot the prices on a map projection
prices = alt.Chart(map_df).mark_circle().encode(
    latitude="CenterLat",
    longitude="CenterLon",
    color=alt.Color("PriceSqr", scale=alt.Scale(scheme="plasma")),
    size="PriceVariance",
    tooltip=["CenterLat", "CenterLon", "PriceSqr", "PriceVariance"]
).project()
prices

alt.Chart(...)

In [8]:
# Plot prices on a map with districts
# Load a chart per district
rootDir = "./geojson"
charts = []
for _, _, geojson_filenames in os.walk(rootDir):
    for geojson_name in geojson_filenames:
        gdf = gpd.read_file(f"./geojson/{geojson_name}", driver="GeoJSON")
        chart = alt.Chart(gdf).mark_geoshape(
            stroke="gray",
            fill=None
        )
        charts.append(chart)

# Add prices on top
prices_legend = alt.Legend(orient="left", labelColor="white", titleColor="white", symbolFillColor="gray", symbolStrokeColor="gray")
prices = alt.Chart(map_df).mark_circle().encode(
    latitude="CenterLat",
    longitude="CenterLon",
    color=alt.Color("PriceSqr", scale=alt.Scale(scheme="plasma"), legend=prices_legend),
    size=alt.Size("PriceVariance", legend=prices_legend),
    href="GoogleMaps",
    tooltip=["CenterLat", "CenterLon", "PriceSqr", "PriceVariance"]
).project()

final_chart = prices
for chart in charts:
    final_chart += chart

final_chart.properties(width=1500, height=1200).configure(background="black")

alt.LayerChart(...)